In [1]:
import Pkg

package_list = ["DataFrames", "CSV",
"JuMP", "Gurobi",
 "LinearAlgebra", "Random", "Printf", "StatsBase", "CategoricalArrays",
  "Plots", "StatsPlots",
  "Distributions", "JLD"]

for pkg_name in package_list
    Pkg.add(pkg_name)
end

    Updating registry at `~/.julia/registries/General.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`
   Resolving package versions...
  No Ch

In [2]:
using DataFrames, CSV
using JLD
using JuMP, Gurobi
using LinearAlgebra, Random, Printf, StatsBase, CategoricalArrays
using Plots, StatsPlots
using Distributions

In [3]:
const GRB_ENV = Gurobi.Env()

Set parameter Username
Academic license - for non-commercial use only - expires 2023-08-18


Gurobi.Env(Ptr{Nothing} @0x00007fdd7740b600, false, 0)

In [4]:
# read in csv file
v = CSV.read("/Users/zachwayne/Documents/GitHub/15093-project/universe/volatility_500.csv", DataFrame)
r = CSV.read("/Users/zachwayne/Documents/GitHub/15093-project/universe/returns_500.csv", DataFrame)
s = CSV.read("/Users/zachwayne/Documents/GitHub/15093-project/universe/sectors_500.csv", DataFrame)
p = CSV.read("/Users/zachwayne/Documents/GitHub/15093-project/universe/price_500.csv", DataFrame)
cor = CSV.read("/Users/zachwayne/Documents/GitHub/15093-project/universe/correlations_500.csv", DataFrame)
cov = CSV.read("/Users/zachwayne/Documents/GitHub/15093-project/universe/covariance_500.csv", DataFrame)
tbill = 0.029339583


0.029339583

In [5]:
stocks=size(p, 2)-1
#stocks = 300


480

In [6]:
model = Model(() -> Gurobi.Optimizer(GRB_ENV));
k = 40
@variable(model, x[1:stocks] >= 0, Int)
@variable(model, z[1:stocks], Bin);
@variable(model, 0<=w[1:stocks]<=.15);
@variable(model,y[1:stocks,1:stocks], Bin);

In [8]:
@constraint(model, sum(x[i]*p[1,i+1] for i=1:stocks) <= 300000);  
@constraint(model, [i=1:stocks], x[i] >= z[i]);
@constraint(model, [i=1:stocks], (x[i]*p[1,i+1]) >= 5000*z[i]);
@constraint(model, [i=1:stocks], w[i] == (x[i]*p[1,i+1])/300000);
@constraint(model, [i=1:stocks], 1000000*w[i] >= z[i]);
@constraint(model, [i=1:stocks], w[i] <= z[i]);
@constraint(model, sum(z[i] for i=1:stocks) == k); 
@constraint(model,[j=2:12],sum(z[i]*s[i,j] for i=1:stocks) <= 5);
@constraint(model, sum(w[i] for i=1:stocks) == 1); 
@constraint(model, w'*r[1:stocks, 2] > .02);

for i = 1:stocks
    for j in 1:stocks
        if i != j
            @constraint(model, y[i,j] >= z[i]+z[j]-1)
        else
            @constraint(model, y[i,j] == 0)
        end
    end
end

# for all stocks we purchase, their c[i,j] must be <= .3
for i=1:stocks
    for j=1:stocks
            @constraint(model, y[i,j]*abs(cor[i,j+1]) <= .3)
    end
end

LoadError: LoadError: At In[8]:10: `@constraint(model, w' * r[1:stocks, 2] > 0.02)`: Unrecognized sense >
in expression starting at In[8]:10

In [256]:
#@objective(model, Max, (sum(w[i] * r[i,2] for i=1:stocks)-tbill)/(sum((w[i]^2) * (v[i,2]^2) for i=1:stocks)+2*(sum(w[i]*w[j]*cov[i,j+1] for i=1:stocks, j=i+1:stocks))));
#@objective(model, Max, (sum((y[i]^2) * (v[i,2]^2) for i=1:stocks)+2*(sum(y[i]cov[i,j+1]*y[j] for i=1:stocks, j=i+1:stocks))));
# Set NonConvex parameter to 2 to solve model.
@objective(model, Min, w'*Matrix(cov[1:stocks, 2:stocks+1])*w )
#

0.0004111649132744796 w[1]² + 0.0004641417482553482 w[2]*w[1] + 0.00017122591161909616 w[3]*w[1] + 0.0001795466450165204 w[4]*w[1] + 0.00019274096766221647 w[5]*w[1] + 0.00029631234126176 w[6]*w[1] + 0.00016416429385027114 w[7]*w[1] + 0.00023837647663924608 w[8]*w[1] + 0.00031948134952964566 w[9]*w[1] + 0.0002631732971637701 w[10]*w[1] + 8.95536924247616e-5 w[11]*w[1] + 0.000363414368521253 w[12]*w[1] + 0.0004570176129702484 w[13]*w[1] + 0.0002626191899064042 w[14]*w[1] + 0.000286581880443767 w[15]*w[1] + 0.00026992962252598657 w[16]*w[1] + 0.0005522253090195911 w[17]*w[1] + 0.00037411027418640707 w[18]*w[1] + 0.00013458782664291986 w[19]*w[1] + 0.0007317629354929385 w[20]*w[1] + 0.0003846380965163316 w[21]*w[1] + 0.00010210732773279921 w[22]*w[1] + 0.000246062936024565 w[23]*w[1] + 0.0003103359866703691 w[24]*w[1] + 0.0003048491850403514 w[25]*w[1] + 0.00026848277291667544 w[26]*w[1] + 0.00022787198842301934 w[27]*w[1] + 0.00019130286179798225 w[28]*w[1] + 0.00015822436409942557 w[29]

In [257]:
optimize!(model);

Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 463214 rows, 231840 columns and 927360 nonzeros
Model fingerprint: 0x78ff14b3
Model has 115440 quadratic objective terms
Variable types: 480 continuous, 231360 integer (230880 binary)
Coefficient statistics:
  Matrix range     [2e-06, 1e+06]
  Objective range  [8e-06, 2e-02]
  QObjective range [6e-08, 2e-01]
  Bounds range     [1e-01, 1e-01]
  RHS range        [3e-01, 3e+05]
Presolve removed 458862 rows and 230400 columns
Presolve time: 3.50s
Presolved: 4352 rows, 1440 columns, 160903 nonzeros
Presolved model has 115440 quadratic objective terms
Variable types: 480 continuous, 960 integer (480 binary)

Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    8558   -3.2410298e+00   2.120674e+04   0.000000e+00      5s
   24652   -6.7864685e+01   2.532943e+03   0.000000e+00     10s
   45134   -6.

In [258]:
obj = objective_value(model)

-0.00687399899038467

In [259]:
z_opt = value.(z)
x_opt = value.(x)
w_opt = value.(w)

480-element Vector{Float64}:
 0.0
 0.0
 0.0
 0.01675871571858724
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.017161042073567705
 0.0
 0.0
 ⋮
 0.0
 0.0
 0.0
 0.017145740254720054
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0

In [260]:
# loop thorugh x and show which stocks we buy
for i=1:stocks
    if z_opt[i] > 0 && w_opt[i] > .02
        println("Stock ", names(p)[i+1], " is ", w_opt[i]*100, "% of portfolio")
    end
end

Stock AMD is 14.981743481953938% of portfolio
Stock KDP is 3.483165229797364% of portfolio
Stock NFLX is 14.86338409423828% of portfolio
Stock PAYC is 5.972133382161458% of portfolio


In [240]:
# find how many of each stock we buy
for i=1:stocks
    if x_opt[i] > 0
        println("Stock ", names(p)[i+1], " is ", x_opt[i], " shares")
    end
end

Stock ABBV is 52.0 shares
Stock AAP is 34.0 shares
Stock ALB is 34.0 shares
Stock ARE is 31.0 shares
Stock AMCR is 457.0 shares
Stock AMD is 487.0 shares
Stock T is 275.0 shares
Stock SCHW is 98.0 shares
Stock CAG is 149.0 shares
Stock CTRA is 343.0 shares
Stock CCI is 34.0 shares
Stock DHR is 23.0 shares
Stock DXCM is 56.0 shares
Stock DG is 25.0 shares
Stock DPZ is 14.0 shares
Stock EW is 56.0 shares
Stock EA is 36.0 shares
Stock ENPH is 29.0 shares
Stock FE is 182.0 shares
Stock GRMN is 44.0 shares
Stock GEN is 244.0 shares
Stock GNRC is 22.0 shares
Stock J is 48.0 shares
Stock JNPR is 237.0 shares
Stock KDP is 342.0 shares
Stock KR is 165.0 shares
Stock LMT is 15.0 shares
Stock MNST is 56.0 shares
Stock NFLX is 85.0 shares
Stock NEM is 89.0 shares
Stock NRG is 148.0 shares
Stock PAYC is 40.0 shares
Stock PCG is 407.0 shares
Stock POOL is 14.0 shares
Stock PGR is 55.0 shares
Stock RSG is 54.0 shares
Stock TMUS is 38.0 shares
Stock VRTX is 22.0 shares
Stock WMT is 36.0 shares
Stock G

In [178]:
# print the sectors we buy
for i=1:stocks
    if x_opt[i] > 0
        #loop through column 1 of s
        for j=1:50
            if s[j,1] == names(p)[i+1]
                for k=2:12
                    if s[j,k] == 1
                        println("Stock ", names(p)[i+1], " is in sector ", names(s)[k])
                    end
                end
            end
        end
    end
end

Stock AMD is in sector Information Technology
